# Importing Libraries

In [1]:
import os 
import librosa 
import numpy as np
import tensorflow as tf
from tensorflow.image import resize

In [2]:
#Loading model
model=tf.keras.models.load_model("./Trained_model.h5")

C:\Users\aryan\anaconda3\envs\tensorflow_env\Lib\site-packages\keras\src\layers\convolutional\base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
C:\Users\aryan\anaconda3\envs\tensorflow_env\Lib\site-packages\keras\src\optimizers\base_optimizer.py:86: UserWarning: Argument `decay` is no longer supported and will be ignored.
  warnings.warn(


In [3]:
classes = ['blues', 'classical','country','disco','hiphop','jazz','metal','pop','reggae','rock']

# Single Audio Preprocessing

In [6]:
#Load and preprocess audio file
def load_and_preprocess_file(file_path,target_shape=(150,150)):
    data=[]
    audio_data,sample_rate=librosa.load(file_path,sr=None)
    chunk_duration = 4  
    overlap_duration = 2 
    chunk_samples = chunk_duration * sample_rate
    overlap_samples = overlap_duration * sample_rate
        
    num_chunks = int(np.ceil((len(audio_data) - chunk_samples) / (chunk_samples - overlap_samples))) + 1

    for i in range(num_chunks):
                    start = i * (chunk_samples - overlap_samples)
                    end = start + chunk_samples
                    # Extract the chunk of audio
                    chunk = audio_data[start:end]
                    # Compute the Mel spectrogram for the chunk
                    mel_spectrogram = librosa.feature.melspectrogram(y=chunk, sr=sample_rate)                    
                    #mel_spectrogram = librosa.feature.melspectrogram(y=audio_data, sr=sample_rate)
                    mel_spectrogram = resize(np.expand_dims(mel_spectrogram, axis=-1), target_shape)
                    data.append(mel_spectrogram)
    return np.array(data)
    

In [10]:
from IPython.display import Audio
file_path="./Lundstroem - Wii music but hip hop.mp3"
y,sr=librosa.load(file_path,sr=44100)
Audio(data=y,rate=sr)

In [7]:
file_path="./Lundstroem - Wii music but hip hop.mp3"
X_test=load_and_preprocess_file(file_path)

In [15]:
X_test

array([[[[3.18750048e+00],
         [6.73184752e-01],
         [3.31948817e-01],
         ...,
         [1.13149178e+00],
         [2.18155122e+00],
         [2.91338277e+00]],

        [[8.86189842e+00],
         [9.64127445e+00],
         [9.10697556e+00],
         ...,
         [1.96210790e+00],
         [1.90002975e+01],
         [9.32184792e+00]],

        [[1.96527596e+01],
         [1.75008621e+01],
         [1.14990711e+01],
         ...,
         [2.36959286e+01],
         [2.18329678e+01],
         [1.50641870e+01]],

        ...,

        [[2.20288071e-04],
         [6.75598411e-10],
         [8.86652032e-08],
         ...,
         [1.24200383e-07],
         [4.10201739e-09],
         [1.20300896e-07]],

        [[8.49110947e-05],
         [4.38367564e-10],
         [3.63712449e-10],
         ...,
         [8.80789552e-10],
         [7.90891075e-10],
         [3.77916898e-08]],

        [[7.55510919e-05],
         [4.62123506e-10],
         [3.68616415e-10],
         ...,
 

# Model prediction

In [26]:
def model_prediction(X_test):
    y_pred=model.predict(X_test)
    predicted_categories=np.argmax(y_pred,axis=1)
    unique_elements,counts=np.unique(predicted_categories,return_counts=True)
    max_count=np.max(counts)
    max_elements=unique_elements[counts==max_count]
    return max_elements[0]

In [27]:
class_index=model_prediction(X_test)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 180ms/step


In [28]:
class_index

4

In [30]:
print("Model prediction of Music Genre-->", classes[class_index])

Model prediction of Music Genre--> hiphop
